# Exercise 4: sWeights and Unfolding

In [1]:
import matplotlib.pyplot as plt
import numba as nb
import numpy as np
from iminuit import Minuit
from iminuit.cost import UnbinnedNLL
from numba_stats import truncexpon, truncnorm
from resample.bootstrap import variance
from scipy.stats import expon, exponnorm

rng = np.random.default_rng(seed=1)

---

## Task 1: sWeights

A 2D experimental distribution with random variables $(m, t)$ has a signal component 
$$
s(m, t) = s_m(m) s_t(t)
$$
and a background component 
$$
b(m, t) = b_m(m) b_t(t).
$$
The allowed range is $0 < m < 1$ and $0 < t < \infty$.

Let $s_m(m)$ be a Gaussian distribution with mean $\mu_s = 0.5$ and standard deviation $\sigma_s = 0.05$. The distribution $s_t(t)$ is an exponential with $\tau_s = 0.1$. The distribution for $b_m(m)$ is a truncated exponential with $\tau_b = 1$. The distribution for $b_t(t)$ is a truncated Gaussian with mean $\mu_b = 0.2$ and $\sigma_b = 0.2$.

We generate a dataset of pairs $(m, t)$ consisting of $2\,000$ signal events and $10\,000$ background events. A simple way to generate samples from a truncated distribution is to generate too many events first (e.g. twice as many) and then cut the distribution back to the desired range and amount.

---

In [2]:
rng = np.random.default_rng(seed=1)


# to produce truncated distributions, generate more than the cut tails
def generate_s(size):
    m = rng.normal(0.5, 0.05, size=2 * size)
    t = rng.exponential(0.1, size=2 * size)
    mask = (0 < m) & (m < 1) & (t > 0) & (t < 1)
    assert np.sum(mask) >= size
    return m[mask][:size], t[mask][:size]


def generate_b(size):
    m = rng.exponential(1, size=2 * size)
    t = rng.normal(0.2, 0.2, size=2 * size)
    mask = (0 < m) & (m < 1) & (t > 0) & (t < 1)
    assert np.sum(mask) >= size
    return m[mask][:size], t[mask][:size]


n_data_s = 2_000
n_data_b = 10_000

data_s_m, data_s_t = generate_s(n_data_s)
data_b_m, data_b_t = generate_b(n_data_b)

data_m = np.append(data_s_m, data_b_m)
data_t = np.append(data_s_t, data_b_t)

# data has shape (N x 2)
data = np.transpose((data_m, data_t))
del data_m, data_t

---

### 1.1

Plot the 2D distribution of $(m, t)$ separately for the signal and background component, and for both components merged. Plot likewise 1D histograms for the projections along $m$ and $t$.

---

---

### 1.2

Fit the mixed distribution in the discriminatory variable $m$ to determine the PDFs and fractions for the signal and background components in the $m$ projection. Assume a truncated gaussian distribution for the signal with unknown parameters $\mu_s$ and $\sigma_s$. Assume a second-order Bernstein polynomial for the background with unknown coefficients.

A second-order Bernstein polynomial for $x \in [0, 1]$ is given by $f(x) = c_1 (1 - x)^2 + 2 c_2 (1 - x) x + c_3 x^2$. See Python implementations below. Bernstein polynomials are ideal for modelling empirical PDFs, because one can guarantee that the polynomial is positive in the domain by requiring $c_i > 0$. This is not the case for other polynomials. One coefficient of the Bernstein polynomial becomes redundant when you compute a normalized PDF. We set $c_1$ = 1 to compensate and fit only $c_2$ and $c_3$.

* Perform the fit with the `iminuit` package, using the `UnbinnedNLL` cost function from `iminuit.cost`.
* Use the `truncnorm` distribution from `numba_stats` to implement the signal PDF.
* Use the `bernstein_pdf` below for the background PDF (it is accelerated with `numba`).
* Normalize the signal and background functions properly to model trunced PDFs.
* Make sure to set appropriate parameter limits in the fit and use good starting values.

---

In [4]:
@nb.njit
def bernstein(x, c1, c2, c3):
    y = 1 - x
    return c1 * y**2 + 2 * c2 * x * y + c3 * x**2


@nb.njit
def bernstein_integral(x, c1, c2, c3):
    y = 1 - x
    return (-c1 * y**3 + c2 * x**2 * (3 - 2 * x) + c3 * x**3) / 3


@nb.njit
def bernstein_pdf(x, c1, c2):
    no = bernstein_integral(1, 1, c1, c2) - bernstein_integral(0, 1, c1, c2)
    return bernstein(x, 1, c1, c2) / no

---

### 1.3 

Compute sWeights and draw them as function of the discriminant variable $m$.

$$
w_s(m) = \frac{W_{bb} \, g_s(m) - W_{sb} \, g_b(m)}{(W_{bb} - W_{sb}) \, g_s(m) + (W_{ss} - W_{sb}) \, g_b(m)}
$$

The $W_{xy}$ are estimated by

$$
\widehat{W}_{xy} = \frac 1 N \sum_i \frac{\hat g_x(m_i) \, \hat g_y(m_i)}{(\hat z \hat g_s(m_i) + (1 - \hat z) \, \hat g_b(m_i))^2}
$$

with signal PDF $g_s$, background PDF $g_b$, and signal fraction $z$.

---

---

### 1.4

Use sWeights to extract the signal component in the control variable. Use a weighted histogram.

_Hint_: The function `numpy.histogram` with the keyword `weights` is useful here. 

---

---

### 1.5

Try to extract the signal component in the discriminant variable $m$ with sWeights in the same as in Task 1.4.

Why does this fail?

---

---

## Task 2: Uncertainties of sWeights

Analytical estimates for the uncertainty of the sWeight estimate are derived in [H. Dembinski, M. Kenzie, C. Langenbruch, M. Schmelling, Nucl.Instrum.Meth.A 1040 (2022) 167270](https://doi.org/10.1016/j.nima.2022.167270) and [C. Langenbruch, Eur.Phys.J.C 82 (2022) 5, 393](https://doi.org/10.1140/epjc/s10052-022-10254-8), but their exact calculation is complicated.

A simple but slightly wrong estimate for the variance of a bin is the sum of weights squared in the bin, $V(n_s) = \sum_i w_{s,i}^2$.

A proper estimate is obtained by repeating the full analysis (including the fit to obtain $\hat z$, $\hat g_s$ and $\hat g_b$) on bootstrapped samples.

We will study both methods in the following. But first we compute the expected signal histogram from the true truncated exponential distribution.

---

In [9]:
# te are bin edges that you need to define in your code,
# you get them as the second return value from numpy.histogram
w_true = n_data_s * np.diff(truncexpon.cdf(te, 0, 1, 0, 0.1))

---

### 2.1

Study the residuals of the sWeighted histogram which estimates the signal in $t$ from Task 1.4 with respect to the true expected signal for the histogram in $t$ that we just computed.

Plot a histogram of the residuals divided by an assumed Poisson error. Is the mean compatible with 0? Is the variance close to 1?

---

---

### 2.2

Compute a variance estimate for each bin in the sWeighted histogram with the simple but insufficient sum-of-weights-squared method.

* Plot the sWeighted histogram again and use the square-root of this variance as an error bar.
* Plot the square-root of this variance as a function of $t$ and compare with an assumed Poisson error.
* Plot the histogram of the residuals divided by the square-root of this variance. How large is the standard deviation of these normalized residuals?

---

---

### 2.3

Compute a variance estimates with the bootstrap method and redo the plots from Task 2.2.

Use the `variance` function from `resample.bootstrap`. To use this function, the whole statistical analysis must be performed by a single pure Python function which obtains the inputs and returns the desired outputs:
```py
def compute(data):
    # all computation including fitting here
    estimates = ...
    return estimates
```
In this case, the `estimates` are the values of the sWeighted histogram in $t$.

_Hint_: The bootstrap is time-consuming. You can speed up the computation of `variance` during development with `size=10`. The bootstrapped variance will have larger fluctuations when `size` is small, but completes faster.

---

---

## Task 3 Fits on sWeighted Distributions

sWeighted data can also be used in fits. A least-squares fit can be performed on a sWeighted histogram if uncertainty estimates from Task 2 are computed, but it is better to perform an unbinned weighted maximum-likelihood fit. We will explore such a fit in this task.

### 3.1

Program a weighted negative log-likelihood function, which uses a truncated exponential density for the signal PDF in $t$ and the previously computed sWeights as weights. Fit the scale parameter of the PDF with `iminuit` (use appropriate limits in the fit). Draw the true signal distribution in $t$, the sWeighted histogram, and the fitted model overlaid.

---

---

### 3.2

Compute an uncertainty estimate $\sigma_\tau$ for the $\tau$ parameter of the truncated exponential distribution using the bootstrap method.

A weighted likelihood is not a normal likelihood and therefore we cannot use the second derivatives to obtain an uncertainty estimate as in the usual case. As previously mentioned in Task 2, it is possible to compute an analytical uncertainty estimates, but the calculation is fairly involved. We therefore use the bootstrap instead, which can be applied to any inference problem.

To apply the bootstrap method, follow steps analog to Task 2.3. You need to modify the `compute` function from Task 2.3. It needs to produce the fitted $\tau$ value instead of an sWeighted histogram. In other words, you need to perform two fits successively in the `compute` function.

---

---

## Task 4: Unfolding

Unfolding is necessary if we want to measure the distribution (a histogram) of some variable $x$, but our detection device randomly distorts $x$. So instead of $x$ we observe the distorted variable $y$. Mathematically, the density of $g(y)$ is given by the convolution integral

$$
g(y) = \int K(y; x) \, f(x) \text{d}x
$$

with the conditional probability density $K(y; x)$ (also called kernel) which is the density of $y$ for a given $x$.

Unfolding is a process to estimate $f(x)$ from a sample of $y$ values. There are many ways to do this, we consider here the best version, parametric unfolding (aka forward folding). In this approach, we simply fit $g(y)$ to the observed sample and thus either extract parameters of $f(x)$ directly or compute a correction function which can be used to convert a histogram of $y$ values into a binned estimate of the $x$ density. Applying this technique requires that parametric models of $f(x)$ and $K(y; x)$ exist. Both may depend on nuisance parameters that can be estimated from the data set.

In our example, $f(x)$ is an exponential distribution. Our detector adds Gaussian noise to $x$ with a constant $\sigma$.

---

In [17]:
tau_true = 0.7
sigma_true = 0.5

x_true = rng.exponential(tau_true, size=1000)
y_obs = rng.normal(x_true, sigma_true)

---

### 4.1

Draw histograms of $x$, $y$ overlaid. Write a Python function that computes the PDF of $y$ and draw it also overlaid.

Use `scipy.stats.exponnorm` to compute the PDF of $y$, which should be a function of $\sigma$ of the Gaussian and the scale parameter $\tau$ of the exponential. Read the `scipy` docs carefully to convert this parametrization to the one accepted by `scipy.stats`.

---

---

### 4.2

Fit your model PDF to the given $y$ sample to estimate the values for $\sigma$ and $\tau$. Restrict $0.05 < \sigma < 0.8$ and $0 < \tau < 2$.

---

---

### 4.3

Now consider a histogram of $y$ values. Compute a scaling factor from the fitted model which computes an $x$-histogram from the the observed counts in the $y$-histogram. This is achieved with a correction factor $c$ for each bin given by

$$
c = \frac{\int_{a}^b f(x) \text{d}x}{\int_{a}^b g(y) \text{d}y}
$$

where $a$ and $b$ are the bin edges in $y$. Draw the correction factors $c_k$ for each bin $k$ and its uncertainty. Compute the latter using the bootstrap method with `resample.bootstrap.variance`.

_Hint_: There is no need to compute these integrals manually, you can use the CDFs of `scipy.stats.expon` and `scipy.stats.exponnorm`.

---

---

### 4.4

Now multiply the correction factors $c_k$ with the bin contents of the $y$-histogram to obtain the unfolded result. Use the bootstrap method to compute the bin-wise errors of this result. Draw overlaid the true $x$ distribution, the histogram of the original $y$ sample, and your unfolded result with error bars.

---